In [1]:
import numpy as np
import matplotlib.pyplot as plt 
import plotly.express as px
import pandas as pd  
import seaborn as sns 
import nbformat
from sklearn.model_selection import train_test_split
from sklearn.linear_model import LinearRegression

In [3]:
carbone = pd.read_csv('/Users/jeandtx/Documents/CODE/M1/DATA VIZ/project 2/pages/carbone.csv')

In [4]:
carbone.columns

Index(['Type Ligne', 'Identifiant de l'élément', 'Structure',
       'Statut de l'élément', 'Nom base français', 'Nom attribut français',
       'Nom frontière français', 'Code de la catégorie', 'Tags français',
       'Unité français', 'Contributeur', 'Programme', 'Url du programme',
       'Source', 'Localisation géographique',
       'Sous-localisation géographique français', 'Date de création',
       'Date de modification', 'Période de validité', 'Incertitude',
       'Réglementations', 'Transparence', 'Qualité', 'Qualité TeR',
       'Qualité GR', 'Qualité TiR', 'Qualité C', 'Qualité P', 'Qualité M',
       'Commentaire français', 'Type poste', 'Nom poste français',
       'Total poste non décomposé', 'CO2f', 'CH4f', 'CH4b', 'N2O',
       'Code gaz supplémentaire 1', 'Valeur gaz supplémentaire 1',
       'Code gaz supplémentaire 2', 'Valeur gaz supplémentaire 2',
       'Code gaz supplémentaire 3', 'Valeur gaz supplémentaire 3',
       'Code gaz supplémentaire 4', 'Valeur gaz sup

In [5]:
carbone.drop([
       "Statut de l'élément", 'Code gaz supplémentaire 2', 'Valeur gaz supplémentaire 2',
       'Code gaz supplémentaire 3', 'Valeur gaz supplémentaire 3',
       'Code gaz supplémentaire 4', 'Valeur gaz supplémentaire 4',
       'Code gaz supplémentaire 5', 'Valeur gaz supplémentaire 5'], axis=1, inplace=True)

In [6]:
# carbone.dropna(thresh=5000, axis=1, inplace=True)

In [7]:
carbone.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 14380 entries, 0 to 14379
Data columns (total 40 columns):
 #   Column                                   Non-Null Count  Dtype  
---  ------                                   --------------  -----  
 0   Type Ligne                               14380 non-null  object 
 1   Identifiant de l'élément                 14380 non-null  int64  
 2   Structure                                14380 non-null  object 
 3   Nom base français                        14380 non-null  object 
 4   Nom attribut français                    13160 non-null  object 
 5   Nom frontière français                   6710 non-null   object 
 6   Code de la catégorie                     14380 non-null  object 
 7   Tags français                            9549 non-null   object 
 8   Unité français                           14304 non-null  object 
 9   Contributeur                             14365 non-null  object 
 10  Programme                                6110 

In [8]:
fig = px.scatter(carbone.select_dtypes([np.number]))
fig.show()

In [9]:
fig = px.histogram(carbone, x='Localisation géographique', y='Total poste non décomposé', histfunc='avg', title='Average CO2 emitting by country')
fig.show()

We can see how France and more generally Europe is good student in emitting of CO2


In [10]:
fig = px.histogram(carbone, x='Localisation géographique', y='Total poste non décomposé', histfunc='sum', title='Sum CO2 emitting by country')
fig.show()

However, if we take the sum we can see that the dataset is mainly about France so we will focus on France and drop the rest of the dataset


In [11]:
carbone.drop(carbone[carbone['Localisation géographique'] == 'Monde'].index, inplace=True)
carbone.drop(carbone[carbone['Localisation géographique'] == 'Europe'].index, inplace=True)
carbone.drop(carbone[carbone['Localisation géographique'] == 'Autre pays du monde'].index, inplace=True)
carbone.drop(['Localisation géographique'], axis=1, inplace=True)

In [12]:
fig = px.histogram(carbone, x='Sous-localisation géographique français', y='Total poste non décomposé', histfunc='avg', title='Sum CO2 emitting by country')
fig.show()


The data is not consistent, again we have to delete the empty rows and columns


In [27]:
carbone.drop(carbone[carbone['Total poste non décomposé'] < 1].index, inplace=True)
fig = px.histogram(carbone, x='Sous-localisation géographique français', y='Total poste non décomposé', histfunc='avg', title='Avg CO2 emitting by departement')
fig.show()

In [14]:
carbone.dropna(thresh=746, axis=1).info()

<class 'pandas.core.frame.DataFrame'>
Index: 1434 entries, 3 to 14294
Data columns (total 14 columns):
 #   Column                                   Non-Null Count  Dtype  
---  ------                                   --------------  -----  
 0   Type Ligne                               1434 non-null   object 
 1   Identifiant de l'élément                 1434 non-null   int64  
 2   Structure                                1434 non-null   object 
 3   Nom base français                        1434 non-null   object 
 4   Nom attribut français                    1164 non-null   object 
 5   Code de la catégorie                     1434 non-null   object 
 6   Unité français                           1434 non-null   object 
 7   Contributeur                             1432 non-null   object 
 8   Sous-localisation géographique français  1434 non-null   object 
 9   Date de création                         1434 non-null   object 
 10  Date de modification                     1404 non-nu

Problem, we now have only 1500 rows our dataset is now significantly smaller. But the data is consistent and usable.

We can actually say that this is the data we had all the rows and columns deleted were just noise.


In [15]:
fig = px.histogram(carbone, x='Date de modification', y='Total poste non décomposé', histfunc='avg', title='Avg CO2 emitting by time', color='Incertitude')
fig.show()

We need to figure out what hapened in November 2014 !


In [16]:
import dash
import dash_core_components as dcc
import dash_html_components as html
import plotly.express as px

# Assuming you have a Dash app instance
app = dash.Dash(__name__)

# Your code
nov2014 = carbone[carbone['Date de modification'] == 'Novembre 2014']

# Array of options for the dropdown
dropdown_options = ['Code de la catégorie', 'Nom attribut français', 'Nom base français', 'Sous-localisation géographique français']

# Dash layout
app.layout = html.Div([
    dcc.Dropdown(
        id='x-dropdown',
        options=[{'label': option, 'value': option} for option in dropdown_options],
        value='Code de la catégorie'
    ),
    dcc.Graph(id='histogram')
])

@app.callback(
    dash.dependencies.Output('histogram', 'figure'),
    [dash.dependencies.Input('x-dropdown', 'value')]
)
def update_histogram(x_value):
    fig = px.histogram(nov2014, y='Total poste non décomposé', x=x_value, color='Incertitude', histfunc='sum')
    return fig

if __name__ == '__main__':
    app.run_server(debug=True)


/Users/jeandtx/Documents/CODE/M1/.venv/lib/python3.9/site-packages/urllib3/__init__.py:34: NotOpenSSLWarning:

urllib3 v2.0 only supports OpenSSL 1.1.1+, currently the 'ssl' module is compiled with 'LibreSSL 2.8.3'. See: https://github.com/urllib3/urllib3/issues/3020

/var/folders/n7/j50r8_zd44l0b2zzdysyhld40000gp/T/ipykernel_98725/2868928806.py:2: UserWarning:


The dash_core_components package is deprecated. Please replace
`import dash_core_components as dcc` with `from dash import dcc`

/var/folders/n7/j50r8_zd44l0b2zzdysyhld40000gp/T/ipykernel_98725/2868928806.py:3: UserWarning:


The dash_html_components package is deprecated. Please replace
`import dash_html_components as html` with `from dash import html`



We can see that the Industry of the department has played a big role in the emission of CO2.

However, we cannot say which department as the department France continentale has been selected. This shows how important the quality of the data is.


In [17]:
fig = px.histogram(carbone, x='Contributeur', y='Total poste non décomposé', histfunc='avg', title='Avg CO2 emitting by time', color='Incertitude')
fig.show()

ADEME is the main source of data for this dataset.


In [18]:
import dash
import dash_core_components as dcc
import dash_html_components as html
import plotly.express as px

# Assuming you have a Dash app instance
app = dash.Dash(__name__)


# Array of options for the dropdown
dropdown_options = ['Code de la catégorie', 'Nom attribut français', 'Nom base français', 'Sous-localisation géographique français']

# Dash layout
app.layout = html.Div([
    dcc.Dropdown(
        id='x-dropdown',
        options=[{'label': option, 'value': option} for option in dropdown_options],
        value='Code de la catégorie'
    ),
    dcc.Graph(id='histogram')
])

@app.callback(
    dash.dependencies.Output('histogram', 'figure'),
    [dash.dependencies.Input('x-dropdown', 'value')]
)
def update_histogram(x_value):
    fig = px.histogram(carbone, y='Total poste non décomposé', x=x_value, color='Incertitude', histfunc='sum')
    return fig

if __name__ == '__main__':
    app.run_server(debug=True)


Finally, we can see that the most responsible of CO2 emission is the industry. Without surprises, this is why the importance of SRE is mandatory for 2020's companies.

source: https://www.data.gouv.fr/fr/datasets/base-carbone-complete-de-lademe-en-francais-v17-0/

After this analysis, we want to know more about the industry and the CO2 emission. We will use the dataset of the industry and the dataset of the CO2 emission to see if we can find a correlation between the two. This is an important part to in a data analysis to combine multiple dataset to check the veractiy of the conclusions we've made.
Here is another dataset to get into the industry carbone print : https://www.inforse.fr/accueil

This dataset is not directly from data.gouv.fr but those are computed features coming from multiple datasets all from data.gouv.fr


In [19]:
industry = pd.read_csv('industry.csv')

In [20]:
fig = px.histogram(industry, x='NAF_SECTION', title='Number of companies by industry in the dataset')
fig.show()

In [21]:
fig = px.histogram(industry, x='NAF_SECTION', title='Tonnes of CO2 produced by industry in the dataset', y='tonnes CO2 scopes 1 & 2', histfunc='sum')
fig.update_layout(yaxis_type="log")
fig.show()

Careful ! This is a log scale click here to set it back to normal


In [22]:
industry.columns

Index(['NAF_SECTION', 'Entité', 'g CO2 / € du secteur',
       'g CO2 /  € de l'entreprise', 'tonnes CO2 scopes 1 & 2'],
      dtype='object')

In [23]:
import plotly.express as px
import plotly.graph_objects as go

# Create your scatter plot with the trendline
fig = px.scatter(industry, x='g CO2 / € du secteur', y="g CO2 /  € de l'entreprise", color='Entité',
                 title='Tonnes of CO2 produced by industry in the dataset')
diagonal = go.Scatter(x=list(range(len(industry))), y=list(range(len(industry))), mode='lines', name='x = y')
fig.add_trace(diagonal)
# Update the y-axis to use a logarithmic scale
fig.update_traces(showlegend=False)
fig.update_layout(yaxis_type="log")

# Show the updated plot
fig.show()


Here this is really interesting to see how bad and good students can be shown in one graph. The ones upper the line are the bad students and the ones below are the good students.

Another way to see this is using a 3D plot


In [24]:
fig = px.scatter_3d(industry, x="g CO2 /  € de l'entreprise", y='g CO2 / € du secteur', z='tonnes CO2 scopes 1 & 2', color='Entité')
fig.update_traces(showlegend=False)
fig.update_layout(yaxis_type="log")
fig.show()